In [ ]:
import matplotlib
%matplotlib notebook
#%matplotlib inline
matplotlib.rcParams['figure.figsize'] = (7, 3)
import numpy as np

# Missing bits from Lecture 1

## More looping

There is of course a `while`-loop

In [ ]:
a = 3

while a > 0:
    print(a)
    a -= 1

## More logic: `if-else-elif`

In [ ]:
today = 'Wednesday'

if today == 'Monday':
    chance_of_party = 'slim to none'
elif today in ['Tuesday', 'Thursday', 'Sunday']:
    chance_of_party = 'poor'
elif today == 'Wednesday':
    chance_of_party = 'possible'
elif today in ['Friday', 'Saturday']:
    chance_of_party = 'likely'
else:
    raise ValueError("'{}' is not a weekday".format(today))
    
print('Current chance of party is', chance_of_party)

There is no `switch` statement in Python!

# Scientific Python

Hannes Ovrén

## Scientific Python Stack

![Some text](images/python_ecosystem.png)
Image source: Fernando Perez

## NumPy

The core numerical array/matrix library

- *Not* part of standard Python install
- `numpy.ndarray` class for N-dimensional arrays
- Mostly C or Fortran
- Functionality for:
  - Linear Algebra
  - Fourier transforms
  - ...


## Example

It is common to alias `numpy` to `np` for less writing

In [ ]:
import numpy as np

Let's create a $2 \times 3$ array

In [ ]:
A = np.array([[1, 2, 3],
              [10, 20, 30]])
A

and transpose it

In [ ]:
A.T

## `numpy.ndarray`
- N-dimensional array
  - `ndarray.ndim`
  - `ndarray.shape`
- item type: `numpy.dtype` - (`float64`, `uint8`, `bool`, ...)

In [ ]:
A = np.random.normal(size=(2,3,2))

In [ ]:
print('#ndim: {}, shape: {}, #elements: {}'.format(A.ndim, A.shape, 
                                                   A.size))
print('dtype: {}, itemsize: {}'.format(A.dtype, A.itemsize))

## Accessing elements

In [ ]:
A = np.array([[1,2,3], [4,5,6], [7,8,9]])
A

In [ ]:
A[1,2]

Access rows

In [ ]:
A[0, :]

In [ ]:
A[0]

Note for MATLAB-users: **zero-indexed** arrays!

Access columns (note the shape!)

In [ ]:
c = A[:, 0]
print(c, c.shape, c.ndim)

Extract parts

In [ ]:
A[:2, :2] # 2x2 block

In [ ]:
A[:, (0, 2)] # first and third columns

## Boolean masks
### Same size mask

In [ ]:
y = np.arange(6).reshape(2, 3)
y

In [ ]:
mask = (y % 2 == 0)
mask

In [ ]:
y[mask]

## Boolean mask, with different shapes
Only first dimensions must match.

Extracting pixels from an image, gives pixel value "vectors"

In [ ]:
image = np.random.randint(0, 255, size=(2,2,3)) # 2x2 RGB image
print(image)

In [ ]:
mask = np.array([[True, False], [False, True]]) # 2x2 mask
image[mask]

## Beware of non-numpy Boolean-masks!

In [ ]:
y = np.array([[1, 2, 3], [4, 5, 6]])
py_mask = [[True, True, False], [False, False, True]]
np_mask = np.array(py_mask)

In [ ]:
print(y[np_mask])
print(y[py_mask])

What happened?

## Sharing data
Most functions/methods return views of an array (sharing data)

In [ ]:
A = np.array([[1, 2, 3], [4, 5, 6]])

middle_col = A[:, 1]
middle_col[:] = 99

A

Use `.copy()` to get a copy

In [ ]:
A = np.array([[1, 2, 3], [4, 5, 6]])
middle_col = A[:, 1].copy()
middle_col[:] = 99
A

## Sharing data: be careful!
Example: We want a function that gives a mean-removed point set

In [ ]:
def normalized(pts):
    m = np.mean(pts, axis=1).reshape(-1, 1)
    pts -= m
    return pts

orig = np.random.normal(10., 1.0, size=(2, 4))
orig

In [ ]:
normalized(orig)

In [ ]:
orig

## Array operations

In [ ]:
A = np.array([[1, 2], [3, 4]])
B = np.ones((2, 2)) # 2x2 of ones
print(A)
print(B)

Addition and subtraction

In [ ]:
A + B

In [ ]:
A - B

What about multiplication?

In [ ]:
print(A)
print(B)

In [ ]:
A * B

## Operations are element-wise!
`numpy.ndarray` is an *array*, not a *matrix*.

For matrix multiplications use `np.dot` or `np.ndarray.dot`

In [ ]:
np.dot(A, B)

In [ ]:
A.dot(B)

Python 3.5 + NumPy 1.10: `@`-operator

In [ ]:
A @ B

## Reshaping

In [ ]:
A = np.arange(10)
print(A, A.shape)

In [ ]:
B = A.reshape((2, 5))
print(B, B.shape)

`A` and `b` points at the same data!

In [ ]:
B[0,0] = 100

print(A)

## Reshaping (cont.)

Automatic calculation of one dimension by setting it to `-1`

In [ ]:
A = np.arange(24)

B = A.reshape(2, -1, 4)
print(B.shape)

Illegal shapes are... illegal :)

In [ ]:
C = A.reshape(2, 4, 4)

## Flattening arrays
- Flatten an array from ND to 1D

In [ ]:
A = np.arange(10).reshape(2,5)

In [ ]:
B = A.ravel()
B

In [ ]:
C = A.flatten() # Copies!
C

In [ ]:
B[0] = 99
C[1] = 100
A

Linear indexing with `ndarray.flat` iterator (no copy)

In [ ]:
A.flat[::2] = 0
A

## Joining arrays
- `hstack`, `vstack`, `dstack`

In [ ]:
a = np.array([1, 2])
b = np.array([3, 4])
c = np.array([5, 6])

In [ ]:
np.hstack((a, b, c))

In [ ]:
np.vstack((a, b, c))

- General function: `concatenate`

In [ ]:
np.concatenate((a, b, c), axis=0)

## Shape matters

In [ ]:
A = np.array([[1, 2]])
B = np.array([[3],[4]])
print(A)
print('+')
print(B)

In [ ]:
A + B

We just witnessed the numpy **broadcasting** system

## Broadcasting
- Quite useful!
- Does *not* copy data!
- Example: scale all image RGB values

In [ ]:
img = np.random.randint(0, 255, size=(256, 256, 3)) # 256x256 RGB image

scaled = img * np.array([0.2, 0.5, 0.3])
print(scaled.shape)

- Example: Remove mean from point set

In [ ]:
points = np.random.normal(loc=3, size=(3, 100)) # N 3D points
m = np.mean(points, axis=1)
print('Original mean: ', m)

shifted = points - m.reshape(3,-1)
print('Shifted mean:', np.mean(shifted, axis=1))

## Broadcasting rules
- Line up starting from last dimension
- Compatible if equal or `1` (else fail!)
- Size `1` dimensions are "stretched" to match
- Then perform operation

<pre>
A      (3d array):  15 x 3 x 5
B      (3d array):  15 x 1 x 5
Result (3d array):  15 x 3 x 5
</pre>

<pre>
A      (4d array):  8 x 1 x 6 x 1
B      (3d array):      7 x 1 x 5
Result (4d array):  8 x 7 x 6 x 5
</pre>

## Creating arrays
- Ranges of integers or floats

In [ ]:
np.linspace(-2, 2, num=10)

In [ ]:
np.arange(10)

- `zeros`, `ones`, `eye`

In [ ]:
np.zeros((2, 5))

In [ ]:
np.eye(3)

- `ones_like`, `zeros_like`

In [ ]:
A = np.eye(4)
A

In [ ]:
np.ones_like(A)

- `empty`, only **allocates** memory (very fast). Array items are whatever was in memory.

In [ ]:
np.empty((2, 5))

## Converting between types
Use the `ndarray.astype()` method:

In [ ]:
A = np.array([[1.5, 2.0, 3.7],
              [1.0, 2.0, 9.99]])
B = A.astype('uint8')
B

This produces a **copy** of the array.

## Memory layout

- Memory is *contiguous* for **new arrays**
- Row-major ("C-order") is default
- Column-major ("Fortran order"/MATLAB) works as well

It is possible to change memory if required (when do you need to?)

- `np.ascontiguous()`
- `np.asfortranarray()` or <br/>
`A = np.array([1,2], order='F')`
- `np.require()` --  The most general way
- Check array properties with `ndarray.flags` attribute

In [ ]:
A = np.array([[1,2], [3, 4]])
b = A[:, 1]
c = np.ascontiguousarray(b)

lines = [str(x.flags).splitlines() for x in (A, b, c)]
print('{:<16s} {:^8s} {:^8s} {:^8s}'.format('', 'A', 'b','c'))
for l in zip(*lines):
    #print(l)
    vals = [s.split(':')[-1].strip()for s in l]
    vals = [v + '*' if not v == vals[0] else v for v in vals]
    flagname = l[0].split(':')[0].strip()
    print('{:<16s} {:^8s} {:^8s} {:^8s}'.format(flagname, *vals))

## Randomness
Module `numpy.random` has most distributions avilable.

In [ ]:
points = np.random.randint(-3, 3, size=(3, 10))

sigma = 0.2
noisy_points = points + np.random.normal(0, sigma, size=points.shape)

print(noisy_points)

## Random sampling
Use `np.shuffle()` or `np.choice()`

In [ ]:
A = np.arange(10)

Randomly select 3 items from `A` without replacement

In [ ]:
np.random.shuffle(A) # shuffle inplace
A[:3]

In [ ]:
np.random.choice(A, 3, replace=False)

## Finding matching samples
- `numpy.nonzero` or `numpy.flatnonzero`

In [ ]:
A = np.random.randint(0, 20, size=10)
indices = np.flatnonzero(A % 3 == 0)

In [ ]:
A

In [ ]:
indices

In [ ]:
A[indices]

## Other functions

- `np.sum()`
- `np.mean()`
- `np.max()`
- `np.argmax()`

We can use either `max()` or `numpy.max()`, the latter is faster!

In [ ]:
N = 10000
%timeit max(np.random.normal(size=N))

In [ ]:
%timeit np.max(np.random.normal(size=N))

## Plotting: matplotlib
- Two different API
  - `matplotlib`: Object-oriented interface
  - `matplotlib.pyplot`: MATLAB-like interface
  - mix and match as you wish!

## `pyplot` example

In [ ]:
import matplotlib.pyplot as plt

x = np.linspace(0, 4*np.pi)
y = np.sin(x)
plt.figure()
plt.plot(x, y, '--')
plt.show()

## Multiple plots
There is no need for MATLABs `hold on`.

In [ ]:
plt.figure()
plt.plot(x, np.sin(x))
plt.plot(x, np.sin(2*x+0.5))
plt.show()

## Legend
Create automatically using `label=` keyword and `legend()`

In [ ]:
y1 = np.sin(x)
y2 = y + np.random.normal(scale=0.1, size=y1.shape)
plt.figure()
plt.plot(x, y1, label='Model')
plt.scatter(x, y2, c='red', marker='x', label='Measurements')
plt.legend(ncol=2)
plt.show()

## `plot()` command
```python
plot(x, y)        # default line style and color
plot(x, y, 'bo')  # blue circle markers
plot(y)           # x is index array 0..N-1
plot(y, 'r+')     # ditto, but with red plusses
```

Some useful keyword arguments
- **color**  *('r', 'red', '#ff0000', ...)*
- **linestyle**   *('-', '--', ...)*
- **linewidth**
- **alpha**
- **label**



## Subplots

In [ ]:
plt.figure()
plt.subplot(2, 1, 1)
plt.plot(x, np.sin(x))
plt.subplot(2, 1, 2)
plt.plot(x, np.sin(2 * x))
plt.show()

## Axis sharing

In [ ]:
plt.figure(figsize=(10, 3))
ax1 = plt.subplot(1, 2, 1)
ax2 = plt.subplot(1, 2, 2, sharex=ax1)
ax1.plot(x, np.sin(x))
ax2.plot(x, 5 * np.sin(2 * (x - np.pi / 2)))
plt.show()

## We can use $\LaTeX$ as well

In [ ]:
plt.figure()
y = np.pi * np.sin(3 * x)
plt.plot(x, y, label='$\pi \cdot \sin(3x)$')
plt.legend()
plt.show()

## Saving plots

### Manually
Press the "save" button :)

### From script
- Replace `show()` with `savefig(filename)`
- Output formats depend on backend
- PNG, PDF, SVG, EPS, PS should be supported by most
- `dpi=` option

## Showing images

`imshow()` defaults to interpolation, but this can be turned off using `interpolation='none'`.

In [ ]:
image = np.random.randint(0, 255, size=(8, 8))
plt.figure(figsize=(6,3))
plt.subplot(1,2,1)
plt.imshow(image)
plt.subplot(1,2,2)
plt.imshow(image, interpolation='none')
plt.show()

## SciPy
Mixed bag of useful things

#### Example modules

- I/O  *(.MAT-files, etc)*
- Linear algebra
- Signal processing
- Image processing
- Sparse matrices
- Optimization
- Interpolation
- ...

See [documentation](http://docs.scipy.org/doc/scipy/reference/) for full list

## Pandas
- `DataFrame` table-like object
- Merge, join, group data frames
- Compute statistics

In [ ]:
import pandas as pd
df = pd.read_csv('pojknamn.csv', skiprows=2, encoding='latin1', 
                 index_col='tilltalsnamn', na_values=['..']).transpose()

In [ ]:
df.head()

In [ ]:
subset = df[['Hannes', 'Adam']]
subset.sum()

### Pandas plotting

In [ ]:
df[['Hannes', 'Andreas', 'Mikael', 'Marcus']].plot()
plt.title('Newly born male names')

## HDF5
Hierarchical Data Format v5

- Dataset: Multidimensional arrays
- Group: Set of Datasets
- Supports metadata
- Path-like identifiers: `/camera1/rgb/frame1`

In [ ]:
import h5py
with h5py.File('hero3_atan.hdf', 'r') as f:
    print('Keys:', list(f.keys()))
    dataset = f['K']
    print(dataset)
    print(dataset.value)

## IPython/Jupyter Notebook
- Write math $x = \frac{1}{2}$ inline or as blocks 
$$
y = \sum_{i=3} x_i^2
$$

- Mix text using *markdown* or HTML with code
- Export to HTML, PDF, presentation, ...
- These presentations are notebooks
- Language support: Python, R, Julia, ...
- Widgets!

## SymPy: Symbolic math

Example: Derivative of $\sin(x) e^x$

In [ ]:
from sympy import init_printing, symbols, exp, sin, diff
init_printing()

x = symbols('x')
diff(sin(x)*exp(x), x)

## OpenCV
- Functions / classes same as C++
- `cv::Mat` represented by `numpy.ndarray`
- Channels in the third dimension
- Plotting
  - OpenCV: `cv2.namedWindow()`, `cv2.imshow()`, ...
  - matplotlib: `plt.imshow()`, ... <span style='color: green'>(highly recommended)</span>

In [ ]:
import cv2
# White square on black background
image = np.zeros((128, 128), dtype='uint8') # CV_8U
image[50:80, 50:80] = 255
image_blurred = cv2.blur(image, ksize=(11, 11))

plt.figure(figsize=(8, 3))
plt.gray()
plt.subplot(1, 2, 1)
plt.imshow(image, interpolation='none')
plt.subplot(1, 2, 2)
plt.imshow(image_blurred, interpolation='none')
plt.show()

## NumPy `dtype`

- Allows structured data arrays

In [ ]:
dt = np.dtype([
        ('name', np.str_, 16),
        ('population', np.uint32)
    ])
print(dt)

In [ ]:
cities = np.array([
        ('Stockholm', 851155),
        ('Göteborg', 516532),
        ('Malmö', 293909),
        ('Linköping', 97428)
    ],dtype=dt)

In [ ]:
np.sum(cities['population'])

In [ ]:
big_cities = cities[cities['population'] > 500000]
print(big_cities['name'])